### 0. Data prep

In [15]:
# Retrieve input
with open('advent-3-0-input.txt', "r", encoding='utf-8') as f:
    instructions = f.readlines()

# input finally retrieved AFTER saving the input file!!!!
print(type(instructions)) 
print(len(instructions))

<class 'list'>
6


In [16]:
# Form just one continuous string to work with
str_=""
for i in range(len(instructions)):
    str_ = "".join([str_, instructions[i]])
len(str_)

18477

### Part 1 

In [41]:
# Let's search the integers to multiply and store them in 2 lists
def int_to_mul(str_x):
    list1 = [] # for int1
    list2 = [] # fort int2
    x="mul("
    k = 4 # to add to index_m to get the character after 'mul('
    index_m = 0
    index_comma = 0
    index_close = 0
    str_wip = str_x

    while index_m >= 0 and index_comma >= 0 and index_close >= 0: # find() returns -1 if not found
        index_m = str_wip.find(x)
        index_comma = str_wip[index_m+k:].find(',')
        index_close = str_wip[index_m+k:].find(')')
        # print(f"index_m = {index_m} and index_comma = {index_comma} and index_close = {index_close}")

        if index_comma > index_close:
            str_wip= str_wip[index_m+k:]
            continue # loop while
            
        else:
            # print(f"index_m+k = {index_m+k} and index_m+k+index_comma-1 = {index_m+k+index_comma-1}")
            int1 = str_wip[index_m+k:index_m+k+index_comma]
            # print(f"int1 ?= {int1} de longueur {len(int1)}")
            if not int1.isdigit(): # int1
                str_wip= str_wip[index_m+k:]
                continue # loop while
            else:
                int2 = str_wip[index_m+k+index_comma+1:index_m+k+index_close]
                # print(f"int2 ?= {int2}")
                if not int2.isdigit(): # int2
                    str_wip= str_wip[index_m+k:]
                    continue # loop while
                else:
                    list1.append(int(int1))
                    list2.append(int(int2))
                    str_wip= str_wip[index_m+k:]

    return list1, list2


In [42]:
import numpy as np

def mul_sum(tuple):
    np_1 = np.array(tuple[0])
    np_2 = np.array(tuple[1])

    np_multiplied = np_1 * np_2

    return np_multiplied.sum()

In [43]:
# Let's check code works with the provided example
str_ex = "xmul(2,4)%&mul[3,7]!@^do_not_mul(5,5)+mul(32,64]then(mul(11,8)mul(8,5))"
tuple_ex = int_to_mul(str_ex) 
tuple_ex, mul_sum(tuple_ex) # expected: ([2,5,11,8], [4,5,8,5]) => 161

(([2, 5, 11, 8], [4, 5, 8, 5]), 161)

In [44]:
# Let's calculate with the input file ! 🥁
tuple_str_ = int_to_mul(str_)
len(tuple_str_[0]), mul_sum(tuple_str_)

(695, 166357705)

### Part 2

In [121]:
# We do the same as above, adding the search for 'do()' and 'don't()'

# Let's search the integers to multiply and store them in 2 lists
def int_to_mul_2(str_x):
    list1 = [] # for int1
    list2 = [] # fort int2
    x="mul("
    k = 4 # to add to index_m to get the character after 'mul('
    index_m = 0
    index_comma = 0
    index_close = 0
    str_wip = str_x
    index_m_abs = index_m
    enabled = True # ⚡️ by default when initiated
    i = 0 # to not add k to index_m_abs for first iteration

    while index_m >= 0 and index_comma >= 0 and index_close >= 0: # find() returns -1 if not found
        # print(f"début boucle: index_m = {index_m} and init index_m_abs = {index_m_abs}")
        index_m = str_wip.find(x)
        index_comma = str_wip[index_m+k:].find(',')
        index_close = str_wip[index_m+k:].find(')')
        print(i)
        if i == 0:
            index_m_abs += index_m # ⚡️NEW VARIABLE for the absolute index on the initial string (no slicing)
        else: 
            index_m_abs += index_m + k 
        # print(f"index_m est là où on trouve mul = {index_m} and now index_m_abs incrémentée à = {index_m_abs}")

        if index_comma > index_close: # syntax corrupted
            str_wip= str_wip[index_m+k:]
            continue # loop while 
        else:
            # print(f"index_m+k = {index_m+k} and index_m+k+index_comma-1 = {index_m+k+index_comma-1}")
            int1 = str_wip[index_m+k:index_m+k+index_comma]
            # print(f"int1 ?= {int1} de longueur {len(int1)}")
            if not int1.isdigit(): # int1 NOT AN INTEGER -> syntax corrupted
                str_wip= str_wip[index_m+k:]
                print("int1 not digit")
                continue # loop while
            else:
                int2 = str_wip[index_m+k+index_comma+1:index_m+k+index_close]
                # print(f"int2 ?= {int2}")
                if not int2.isdigit(): # int2 NOT AN INTEGER -> syntax corrupted
                    str_wip= str_wip[index_m+k:]
                    print("int2 not digit")
                    continue # loop while
                else: # only case where syntax is correct
                    # ⚡️ Let's add the checks for DO() / DON'T() here
                    # We check for the section BEFORE mul(int1, int2)
                    # print(f"index_m_abs = {index_m_abs}")
                    str_to_check = str_x[:index_m_abs] # we use the absolute index
                    print(f"str_to_check = {str_to_check}")
                    check_=str_to_check.find("do()")
                    check_dont=str_to_check.find("don't()")
                    index_do = str_to_check[::-1].find(")(od") # we check in reverse [::-1] so find() gets the closest occurrence
                    index_dont = str_to_check[::-1].find(")(t'nod")
                    # print(f"index_do = {index_do}, index_dont = {index_dont}")
                    if index_do == -1 and index_dont > 0: # do is not found whereas don't is found
                        enabled = False
                        print(f'case IF: index_do == -1 and index_dont > 0 - do not append {int1} and {int2}')
                    elif index_do > 0 and index_dont > 0 and index_do > index_dont: # "don't()" is closer
                        enabled = False
                        print(f'case ELIF: index_do > 0 and index_dont > 0 and index_do > index_dont - do not append {int1} and {int2}')
                    else: # in all other cases, do() is closer and we can append int1 and int2 for future multiplication 
                        # this remains unchanged if we don't disable instructions
                        list1.append(int(int1))
                        list2.append(int(int2))
                        print(f'ELSE: append {int1} and {int2} resp. in list1 = {list1} and list2 = {list2}')
                        enabled = True
                    print(enabled)
                str_wip= str_wip[index_m+k:]
        i += 1
    return list1, list2



In [52]:
str_ex2 = "xmul(2,4)&mul[3,7]!^don't()_mul(5,5)+mul(32,64](mul(11,8)undo()?mul(8,5))"

In [119]:
# Let's check with str_ex
tuple_ex_2 = int_to_mul_2(str_ex2) 

# We re-use the multiplication function defined in part 1
tuple_ex_2, mul_sum(tuple_ex_2) # expected: 48 (2*4 + 8*5)

0
str_to_check = x
ELSE: append 2 and 4 resp. in list1 = [2] and list2 = [4]
True
1
str_to_check = xmul(2,4)&mul[3,7]!^don't()_
case IF: index_do == -1 and index_dont > 0 - do not append 5 and 5
False
2
B2
2
str_to_check = xmul(2,4)&mul[3,7]!^don't()_mul(5,5)+mul(32,64](
case IF: index_do == -1 and index_dont > 0 - do not append 11 and 8
False
3
str_to_check = xmul(2,4)&mul[3,7]!^don't()_mul(5,5)+mul(32,64](mul(11,8)undo()?
ELSE: append 8 and 5 resp. in list1 = [2, 8] and list2 = [4, 5]
True
4
B1


(([2, 8], [4, 5]), 48)

In [122]:
# On teste avec l'input
tuple_2 = int_to_mul_2(str_) 

# We re-use the multiplication function defined in part 1
len(tuple_2[0]), mul_sum(tuple_2) # expected: 48 (2*4 + 8*5)

0
str_to_check = %why();how()*-],+!
ELSE: append 696 and 865 resp. in list1 = [696] and list2 = [865]
True
1
str_to_check = %why();how()*-],+!mul(696,865)why()from()how():,;{where()
ELSE: append 170 and 685 resp. in list1 = [696, 170] and list2 = [865, 685]
True
2
str_to_check = %why();how()*-],+!mul(696,865)why()from()how():,;{where()mul(170,685)who()how()*from(881,957)?&select()
ELSE: append 894 and 569 resp. in list1 = [696, 170, 894] and list2 = [865, 685, 569]
True
3
str_to_check = %why();how()*-],+!mul(696,865)why()from()how():,;{where()mul(170,685)who()how()*from(881,957)?&select()mul(894,569):
ELSE: append 648 and 114 resp. in list1 = [696, 170, 894, 648] and list2 = [865, 685, 569, 114]
True
4
str_to_check = %why();how()*-],+!mul(696,865)why()from()how():,;{where()mul(170,685)who()how()*from(881,957)?&select()mul(894,569):mul(648,114);[:from(657,891)how()
ELSE: append 740 and 402 resp. in list1 = [696, 170, 894, 648, 740] and list2 = [865, 685, 569, 114, 402]
True
5
str_to_che

(372, 89678113)